In [ ]:
import json
import string, re, pickle
import numpy as np
from nltk.tokenize import word_tokenize
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, LSTM, Bidirectional, TimeDistributed, Dense
import spacy
import nltk


nltk.download ('punkt')
nltk.download ('averaged_perceptron_tagger')
nltk.download ('maxent_ne_chunker')
nltk.download ('words')

[nltk_data] Downloading package punkt to /home/akeon/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /home/akeon/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     /home/akeon/nltk_data...
[nltk_data]   Package maxent_ne_chunker is already up-to-date!
[nltk_data] Downloading package words to /home/akeon/nltk_data...
[nltk_data]   Package words is already up-to-date!


True

In [ ]:
import spacy

# Load model multibahasa yang mendukung Indonesia
nlp = spacy.load("xx_ent_wiki_sm")

# Contoh teks
text = "Kerajaan Aceh mencapai puncak kejayaannya di bawah pemerintahan Sultan Iskandar Muda pada abad ke-17. Aceh menjadi pusat perdagangan dan kebudayaan Islam di wilayah Nusantara."

# Proses teks dengan model
doc = nlp(text)

# Cetak entitas yang dikenali
for ent in doc.ents:
    print(ent.text, ent.label_)
    

# def generate_ner_context(text):
#     # Load the pretrained spaCy model (small Indo model or use multilingual model if needed)
#     nlp = spacy.load("xx_ent_wiki_sm")  # Load multilingual model
    
#     # Process the text
#     doc = nlp(text)
    
#     # Tokenization and Named Entity Recognition (NER)
#     tokens = [token.text for token in doc]
#     ner_tags = []
#     for token in doc:
#         if token.ent_type_:
#             ner_tags.append(f"B-{token.ent_type_}")
#         else:
#             ner_tags.append("O")
    
#     return tokens, ner_tags

# # Example input context
# context = "Perang Diponegoro berlangsung dari tahun 1825 hingga 1830. Perang ini dipimpin oleh Pangeran Diponegoro melawan pemerintah kolonial Belanda di Jawa Tengah."

# # Generate NER and tokens
# tokens, ner_tags = generate_ner_context(context)

# # Construct the JSON result
# result = {
#     "context": context,
#     "context_tokens": tokens,
#     "context_ner": ner_tags,
#     "question_posibility": [
#         {
#             "type": "true_false",
#             "question": "Perang Diponegoro berlangsung selama lima tahun.",
#             "answer": "True"
#         },
#         {
#             "type": "true_false",
#             "question": "Perang Diponegoro berakhir pada tahun 1850.",
#             "answer": "False"
#         }
#     ]
# }

# # Output the result
# import json
# print(json.dumps(result, indent=4, ensure_ascii=False))

Kerajaan Aceh PER
Iskandar Muda PER
ke-17 MISC
Islam MISC
Nusantara LOC


In [2]:
dataset = [
    {
        "context": "Pertempuran Surabaya terjadi pada 10 November 1945 antara pasukan Indonesia melawan pasukan sekutu Inggris yang berusaha mengambil alih kota setelah Jepang menyerah dalam Perang Dunia II. Pertempuran ini dikenang sebagai Hari Pahlawan di Indonesia.",
        "context_tokens": [
            "Pertempuran", "Surabaya", "terjadi", "pada", "10", "November", "1945",
            "antara", "pasukan", "Indonesia", "melawan", "pasukan", "sekutu", "Inggris",
            "yang", "berusaha", "mengambil", "alih", "kota", "setelah", "Jepang", "menyerah",
            "dalam", "Perang", "Dunia", "II", ".", "Pertempuran", "ini", "dikenang", "sebagai",
            "Hari", "Pahlawan", "di", "Indonesia", "."
        ],
        "context_ner": [
            "O", "B-LOC", "O", "O", "B-DATE", "I-DATE", "I-DATE",
            "O", "O", "B-LOC", "O", "O", "O", "B-LOC",
            "O", "O", "O", "O", "O", "O", "B-LOC", "O",
            "O", "B-MISC", "I-MISC", "I-MISC", "O", "O", "O", "O", "O",
            "O", "O", "O", "B-LOC", "O"
        ],
        "question_posibility": [
            {
                "type": "fill_in_the_blank",
                "question": "Pertempuran Surabaya terjadi pada tanggal _______.",
                "answer": "10 November 1945"
            },
            {
                "type": "multiple_choice",
                "question": "Pasukan yang dihadapi Indonesia dalam Pertempuran Surabaya berasal dari negara apa?",
                "options": ["Jepang", "Belanda", "Inggris", "Australia"],
                "answer": "Inggris"
            },
            {
                "type": "true_false",
                "question": "Pertempuran Surabaya diperingati sebagai Hari Pahlawan di Indonesia.",
                "answer": "True"
            }
        ]
    },
    {
        "context": "Perang Diponegoro berlangsung dari tahun 1825 hingga 1830. Perang ini dipimpin oleh Pangeran Diponegoro melawan pemerintah kolonial Belanda di Jawa Tengah.",
        "context_tokens": [
            "Perang", "Diponegoro", "berlangsung", "dari", "tahun", "1825", "hingga", "1830", ".",
            "Perang", "ini", "dipimpin", "oleh", "Pangeran", "Diponegoro", "melawan",
            "pemerintah", "kolonial", "Belanda", "di", "Jawa", "Tengah", "."
        ],
        "context_ner": [
            "O", "B-PER", "O", "O", "O", "B-DATE", "O", "B-DATE", "O",
            "O", "O", "O", "O", "B-PER", "I-PER", "O",
            "O", "O", "B-LOC", "O", "O", "B-LOC", "O"
        ],
        "question_posibility": [
            {
                "type": "true_false",
                "question": "Perang Diponegoro berlangsung selama lima tahun.",
                "answer": "True"
            },
            {
                "type": "true_false",
                "question": "Perang Diponegoro berakhir pada tahun 1850.",
                "answer": "False"
            }
        ]
    }
]

In [3]:
contexts_tokens = []
contexts_ner = []
questions = []
answers = []
qtypes = []

for entry in dataset:
    contexts_tokens.append(entry["context_tokens"])
    contexts_ner.append(entry["context_ner"])
    qa = entry["question_posibility"][0]  # pilih soal pertama
    questions.append(qa["question"])
    answers.append(qa["answer"])
    qtypes.append(qa["type"])  # misalnya "fill_in_the_blank"

# ----------------------------
# Tokenisasi untuk Kata
# ----------------------------
# Kita gabungkan semua teks dari context (dari tokens), pertanyaan, dan jawaban
all_texts = []
for tokens in contexts_tokens:
    all_texts.append(" ".join(tokens))
all_texts += questions
all_texts += answers

tokenizer = Tokenizer(oov_token="<OOV>")
tokenizer.fit_on_texts(all_texts)

# Ubah context_tokens menjadi sequence angka
context_sequences = [tokenizer.texts_to_sequences([" ".join(tokens)])[0] for tokens in contexts_tokens]
question_sequences = tokenizer.texts_to_sequences(questions)
answer_sequences = tokenizer.texts_to_sequences(answers)

# Padding sequence ke panjang tetap
MAX_LENGTH = 50  # sesuaikan dengan panjang teks maksimum yang diinginkan
context_padded = pad_sequences(context_sequences, maxlen=MAX_LENGTH, padding="post", truncating="post")
question_padded = pad_sequences(question_sequences, maxlen=MAX_LENGTH, padding="post", truncating="post")
answer_padded = pad_sequences(answer_sequences, maxlen=MAX_LENGTH, padding="post", truncating="post")

In [4]:
# ----------------------------
# Tokenisasi untuk Label NER
# ----------------------------
# Kumpulkan semua label NER untuk membangun mapping label ke indeks
all_ner_labels = []
for ner_seq in contexts_ner:
    all_ner_labels += ner_seq

ner_labels_set = sorted(list(set(all_ner_labels)))
# Contoh: ['B-DATE', 'B-LOC', 'B-MISC', 'B-PER', 'I-DATE', 'I-MISC', 'I-PER', 'O']
ner2idx = {label: idx for idx, label in enumerate(ner_labels_set)}
idx2ner = {idx: label for label, idx in ner2idx.items()}

# Ubah label NER ke dalam bentuk sequence angka
ner_sequences = []
for ner_seq in contexts_ner:
    seq = [ner2idx[label] for label in ner_seq]
    ner_sequences.append(seq)

# Padding sequence label NER (gunakan nilai default misal label "O")
ner_padded = pad_sequences(ner_sequences, maxlen=MAX_LENGTH, padding="post", truncating="post", value=ner2idx["O"])

# ----------------------------
# Label Tipe Soal
# ----------------------------
qtype_dict = {"fill_in_the_blank": 0, "true_false": 1, "multiple_choice": 2}
qtype_labels = np.array([qtype_dict[q] for q in qtypes])

In [5]:
# ----------------------------
# Split Data Training dan Validation
# ----------------------------
(context_train, context_val, 
 question_train, question_val, 
 answer_train, answer_val, 
 qtype_train, qtype_val,
 ner_train, ner_val) = train_test_split(
    context_padded, question_padded, answer_padded, qtype_labels, ner_padded,
    test_size=0.2, random_state=42
)

In [6]:
# ----------------------------
# Parameter Model
# ----------------------------
VOCAB_SIZE = len(tokenizer.word_index) + 1
EMBEDDING_DIM = 300
LSTM_UNITS = 256
BATCH_SIZE = 16
EPOCHS = 10
NUM_NER_TAGS = len(ner2idx)

# ----------------------------
# Arsitektur Model Multi-Output
# ----------------------------

# Encoder: Input context
context_input = Input(shape=(MAX_LENGTH,), name="context_input")
context_embedding = Embedding(input_dim=VOCAB_SIZE, output_dim=EMBEDDING_DIM, mask_zero=True, name="context_embedding")(context_input)
encoder_lstm = LSTM(LSTM_UNITS, return_state=True, name="encoder_lstm")
encoder_output, state_h, state_c = encoder_lstm(context_embedding)

# Branch untuk pembuatan soal (Question Decoder)
question_decoder_input = Input(shape=(MAX_LENGTH,), name="question_decoder_input")
question_embedding = Embedding(input_dim=VOCAB_SIZE, output_dim=EMBEDDING_DIM, mask_zero=True, name="question_embedding")(question_decoder_input)
question_lstm = LSTM(LSTM_UNITS, return_sequences=True, return_state=True, name="question_lstm")
question_output, _, _ = question_lstm(question_embedding, initial_state=[state_h, state_c])
question_dense = Dense(VOCAB_SIZE, activation="softmax", name="question_output")(question_output)

# Branch untuk pembuatan jawaban (Answer Decoder)
answer_lstm = LSTM(LSTM_UNITS, return_sequences=True, return_state=True, name="answer_lstm")
answer_output, _, _ = answer_lstm(context_embedding, initial_state=[state_h, state_c])
answer_dense = Dense(VOCAB_SIZE, activation="softmax", name="answer_output")(answer_output)

# Branch untuk klasifikasi tipe soal
type_dense = Dense(128, activation="relu")(encoder_output)
question_type_output = Dense(3, activation="softmax", name="question_type_output")(type_dense)

# Branch untuk NER: Menggunakan context_embedding untuk melakukan sequence tagging
ner_lstm = Bidirectional(LSTM(LSTM_UNITS, return_sequences=True, recurrent_dropout=0.1), name="ner_lstm")(context_embedding)
ner_output = TimeDistributed(Dense(NUM_NER_TAGS, activation="softmax"), name="ner_output")(ner_lstm)

# Gabungkan semua branch dalam satu model multi-output
model = Model(
    inputs=[context_input, question_decoder_input],
    outputs=[question_dense, answer_dense, question_type_output, ner_output]
)

model.compile(
    optimizer="adam",
    loss={
        "question_output": "sparse_categorical_crossentropy",
        "answer_output": "sparse_categorical_crossentropy",
        "question_type_output": "sparse_categorical_crossentropy",
        "ner_output": "sparse_categorical_crossentropy"
    },
    metrics={
        "question_output": ["accuracy"],
        "answer_output": ["accuracy"],
        "question_type_output": ["accuracy"],
        "ner_output": ["accuracy"]
    }
)

model.summary()

# ----------------------------
# Training Model
# ----------------------------
model.fit(
    [context_train, question_train],
    {
        "question_output": question_train,
        "answer_output": answer_train,
        "question_type_output": qtype_train,
        "ner_output": ner_train
    },
    batch_size=BATCH_SIZE,
    epochs=EPOCHS,
    validation_data=(
        [context_val, question_val],
        {
            "question_output": question_val,
            "answer_output": answer_val,
            "question_type_output": qtype_val,
            "ner_output": ner_val
        }
    )
)

# Simpan model dan tokenizer bila diperlukan
model.save("lstm_multi_output_ner_model.keras")
with open("tokenizer.pkl", "wb") as handle:
    pickle.dump(tokenizer, handle, protocol=pickle.HIGHEST_PROTOCOL)

2025-03-23 15:06:59.338033: E external/local_xla/xla/stream_executor/cuda/cuda_driver.cc:152] failed call to cuInit: INTERNAL: CUDA error: Failed call to cuInit: UNKNOWN ERROR (303)


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ context_input       │ (None, 50)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_decoder_i… │ (None, 50)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ context_embedding   │ (None, 50, 300)   │     15,600 │ context_input[0]… │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal           │ (None, 50)        │          0 │ context_input[0]… │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_embedding  │ (None, 50, 300)   │     15,600 │ question_decoder… │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ encoder_lstm (LSTM) │ [(None, 256),     │    570,368 │ context_embeddin… │
│                     │ (None, 256),      │            │ not_equal[0][0]   │
│                     │ (None, 256)]      │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_lstm       │ [(None, 50, 256), │    570,368 │ question_embeddi… │
│ (LSTM)              │ (None, 256),      │            │ encoder_lstm[0][… │
│                     │ (None, 256)]      │            │ encoder_lstm[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ answer_lstm (LSTM)  │ [(None, 50, 256), │    570,368 │ context_embeddin… │
│                     │ (None, 256),      │            │ encoder_lstm[0][… │
│                     │ (None, 256)]      │            │ encoder_lstm[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 128)       │     32,896 │ encoder_lstm[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_lstm            │ (None, 50, 512)   │  1,140,736 │ context_embeddin… │
│ (Bidirectional)     │                   │            │ not_equal[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_output     │ (None, 50, 52)    │     13,364 │ question_lstm[0]… │
│ (Dense)             │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ answer_output       │ (None, 50, 52)    │     13,364 │ answer_lstm[0][0] │
│ (Dense)             │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_type_outp… │ (None, 3)         │        387 │ dense[0][0]       │
│ (Dense)             │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_output          │ (None, 50, 8)     │      4,104 │ ner_lstm[0][0],   │
│ (TimeDistributed)   │                   │            │ not_equal[0][0]   │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 2,947,155 (11.24 MB)

 Trainable params: 2,947,155 (11.24 MB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/10


2025-03-23 15:07:06.004502: E tensorflow/core/util/util.cc:131] oneDNN supports DT_BOOL only on platforms with AVX-512. Falling back to the default Eigen-based implementation if present.


1/1 ━━━━━━━━━━━━━━━━━━━━ 8s 8s/step - answer_output_accuracy: 0.0000e+00 - answer_output_loss: 3.9473 - loss: 11.0828 - ner_output_accuracy: 0.0800 - ner_output_loss: 2.0766 - question_output_accuracy: 0.0400 - question_output_loss: 3.9452 - question_type_output_accuracy: 0.0000e+00 - question_type_output_loss: 1.1138 - val_answer_output_accuracy: 0.3200 - val_answer_output_loss: 3.9260 - val_loss: 11.0343 - val_ner_output_accuracy: 0.8600 - val_ner_output_loss: 2.0489 - val_question_output_accuracy: 0.0000e+00 - val_question_output_loss: 3.9441 - val_question_type_output_accuracy: 0.0000e+00 - val_question_type_output_loss: 1.1153
Epoch 2/10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 300ms/step - answer_output_accuracy: 0.6800 - answer_output_loss: 3.8844 - loss: 10.8637 - ner_output_accuracy: 0.7800 - ner_output_loss: 2.0194 - question_output_accuracy: 0.0800 - question_output_loss: 3.9047 - question_type_output_accuracy: 1.0000 - question_type_output_loss: 1.0550 - val_answer_output_accuracy: 0.58